# Create water extent maps with Sentinel-2 

* **[Sign up to the DEA Sandbox](https://app.sandbox.dea.ga.gov.au/)** to run this notebook interactively from a browser
* **Compatibility:** Notebook currently compatible with `DEA Sandbox` environment
* **Products used:** 
[ga_s2am_ard_3](https://explorer.dea.ga.gov.au/products/ga_s2am_ard_3)  [ga_s2bm_ard_3](https://explorer.dea.ga.gov.au/products/ga_s2bm_ard_3)

## Getting started
To run this analysis, run all the cells in the notebook, starting with the "Load packages" cell. 

### Load packages
Import Python packages that are used for the analysis.

In [2]:
%matplotlib inline

import datacube
import matplotlib.pyplot as plt
import numpy as np
import geopandas as gpd
import xarray as xr

from dea_tools.bandindices import calculate_indices
from dea_tools.dask import create_local_dask_cluster
from dea_tools.datahandling import load_ard
from dea_tools.plotting import display_map, xr_animation
from odc.geo.geom import Geometry

from IPython.display import Image
from matplotlib.colors import ListedColormap
from matplotlib.patches import Patch

### Connect to the datacube

Activate the datacube database, which provides functionality for loading and displaying stored Earth observation data.

In [3]:
dc = datacube.Datacube(app="S2_water_extent")

## Set up a Dask cluster

Dask can be used to better manage memory use and conduct the analysis in parallel. 
For an introduction to using Dask with Digital Earth Australia, see the [Dask notebook](../Beginners_guide/09_Parallel_processing_with_Dask.ipynb).

>**Note**: We recommend opening the Dask processing window to view the different computations that are being executed; to do this, see the *Dask dashboard in JupyterLab* section of the [Dask notebook](../Beginners_guide/09_Parallel_processing_with_Dask.ipynb).

To activate Dask, set up the local computing cluster using the cell below.

In [4]:
client = create_local_dask_cluster(spare_mem='1Gb', display_client=True, return_client=True)

<Client: 'tcp://127.0.0.1:41459' processes=1 threads=2, memory=14.07 GiB>

### Open shapefile of area of interest

Shapefile should be uploaded to Sandbox Environment

In [6]:
vector_file = 'mm_floodplain_boundary_Eflow_2014_2015.shp' #The vector file you uploaded to your Sandbox


polygon_to_drill = gpd.read_file(vector_file)

# Select polygon
shapely_geometry = polygon_to_drill.iloc[0].geometry

# Convert to Geometry object with CRS information
geom = Geometry(geom=shapely_geometry, crs=polygon_to_drill.crs)

geom

## Load cloud-masked satellite data

The code below will create a query dictionary for our region of interest, and then load Sentinel-2 satellite data.
For more information on loading data, see the [Loading data notebook](../Beginners_guide/04_Loading_data.ipynb).

In [7]:
## Create a query object
query = {
    "geopolygon": geom,
    "resolution": (-10, 10),
    "time": ("2025-06-01", "2025-06-30"),
    "dask_chunks": {"time": 20, "x": 1000, "y": 2000},
    "output_crs": "EPSG:3577",
}

# load Sentinel 2 data with less than 10% cloud cover
ds = load_ard(
    dc=dc,
    products=["ga_s2bm_ard_3", "ga_s2cm_ard_3"],
    measurements=["nbart_swir_3", "nbart_green", "nbart_red", 'nbart_nir_1', 
                                "nbart_swir_2","oa_fmask"
                  ],
    cloud_mask="s2cloudless",
    min_gooddata=0.9,
    group_by="solar_day",
    **query
)



Finding datasets
    ga_s2bm_ard_3
    ga_s2cm_ard_3
Counting good quality pixels for each time step using s2cloudless


/env/lib/python3.10/site-packages/rasterio/warp.py:387: NotGeoreferencedWarning: Dataset has no geotransform, gcps, or rpcs. The identity matrix will be returned.
  dest = _reproject(


Filtering to 3 out of 11 time steps with at least 90.0% good quality pixels
Applying s2cloudless pixel quality/cloud mask
Returning 3 time steps as a dask array


## Calculate the Fisher water index, binarise water

In [8]:
# Calculate the chosen vegetation proxy index and add it to the loaded data set
ds['fwi'] = 1.7204 + 171*(ds.nbart_green/10000) + 3*(ds.nbart_red/10000) - 70*(ds.nbart_nir_1/10000) - 45*(ds.nbart_swir_2/10000)-71*(ds.nbart_swir_3/10000)


ds['water'] = (ds['fwi'] >= -18.31).astype(np.int8) # Thresholds: -12.67 for Narran Lakes (Lower Balonne) // -18.31 for Macquarie Marshes 

ds

<xarray.Dataset> Size: 8GB
Dimensions:       (time: 3, y: 16426, x: 5380)
Coordinates:
  * time          (time) datetime64[ns] 24B 2025-06-05T00:15:39.781701 ... 20...
  * y             (y) float64 131kB -3.383e+06 -3.383e+06 ... -3.547e+06
  * x             (x) float64 43kB 1.438e+06 1.438e+06 ... 1.492e+06 1.492e+06
    spatial_ref   int32 4B 3577
Data variables:
    nbart_swir_3  (time, y, x) float32 1GB dask.array<chunksize=(3, 2000, 1000), meta=np.ndarray>
    nbart_green   (time, y, x) float32 1GB dask.array<chunksize=(3, 2000, 1000), meta=np.ndarray>
    nbart_red     (time, y, x) float32 1GB dask.array<chunksize=(3, 2000, 1000), meta=np.ndarray>
    nbart_nir_1   (time, y, x) float32 1GB dask.array<chunksize=(3, 2000, 1000), meta=np.ndarray>
    nbart_swir_2  (time, y, x) float32 1GB dask.array<chunksize=(3, 2000, 1000), meta=np.ndarray>
    oa_fmask      (time, y, x) float32 1GB dask.array<chunksize=(3, 2000, 1000), meta=np.ndarray>
    fwi           (time, y, x) float32 1GB dask.array<chunksize=(3, 2000, 1000), meta=np.ndarray>
    water         (time, y, x) int8 265MB dask.array<chunksize=(3, 2000, 1000), meta=np.ndarray>
Attributes:
    crs:           EPSG:3577
    grid_mapping:  spatial_ref

## Iterate through dates and write tiffs

In [ ]:
%%time
from datacube.utils.cog import write_cog

band = "water"

waterds = ds[band].compute()

for i in range(len(waterds.time)):

    # We will use the date of the satellite image to name the GeoTIFF
    date = ds.isel(time=i).time.dt.strftime("%Y%m%d").data
    print(f"Writing {date} for band {band}")

    # Select the individual timestep as a xr.DataArray
    singletimestamp_da = waterds.isel(time=i)

    # Write GeoTIFF
    write_cog(geo_im=singletimestamp_da, fname=f"MM{date}_S2_DEA.tif", overwrite=True)

Writing 20250605 for band water
Writing 20250615 for band water


In [12]:
client.close()

---

## Additional information

**License:** The code in this notebook is licensed under the [Apache License, Version 2.0](https://www.apache.org/licenses/LICENSE-2.0). 
Digital Earth Australia data is licensed under the [Creative Commons by Attribution 4.0](https://creativecommons.org/licenses/by/4.0/) license.

**Contact:** If you need assistance, please post a question on the [Open Data Cube Discord chat](https://discord.com/invite/4hhBQVas5U) or on the [GIS Stack Exchange](https://gis.stackexchange.com/questions/ask?tags=open-data-cube) using the `open-data-cube` tag (you can view previously asked questions [here](https://gis.stackexchange.com/questions/tagged/open-data-cube)).

If you would like to report an issue with this notebook, you can file one on [GitHub](https://github.com/GeoscienceAustralia/dea-notebooks).

**Last modified:** July 2024

**Compatible datacube version:**

In [9]:
print(datacube.__version__)

1.8.19


## Tags
<!-- Browse all available tags on the DEA User Guide's [Tags Index](https://knowledge.dea.ga.gov.au/genindex/) -->